Анализ дубликатов в датасете

In [1]:
import re
import json
import glob
from pathlib import Path

In [2]:
json_filenames = [filename for filename in glob.glob("cleaned\*.json")]

In [3]:
len(json_filenames)

1413

In [ ]:
def extract_last_digits_from_url(url):
  """
  Извлекает последние цифры из URL-адреса, используя регулярное выражение.

  Аргументы:
    url: URL-адрес в виде строки.

  Возвращает:
    Строка, содержащая последние цифры из URL-адреса, или None, если цифры не найдены.
  """
  match = re.search(r'/(\d+)/?$', url)
  if match:
    return int(match.group(1))
  else:
    return None

In [10]:
# def compare_dicts(dict1, dict2):
#     """
#     Сравнивает два словаря на равенство, включая вложенные словари.

#     Аргументы:
#         dict1: Первый словарь.
#         dict2: Второй словарь.

#     Возвращает:
#         True, если словари равны; False в противном случае.
#     """
#     if dict1.keys() != dict2.keys():
#         return False

#     for key in dict1:
#         val1 = dict1[key]
#         val2 = dict2[key]

#         # Проверка на вложенные словари
#         if isinstance(val1, dict) and isinstance(val2, dict):
#             if not compare_dicts(val1, val2):
#                 return False
#         elif val1 != val2:
#             return False

#     return True

def compare_dicts(dict1, dict2, level=0):
    """
    Сравнивает два словаря на равенство, включая вложенные словари,
    с выводом отладочной информации.

    Аргументы:
        dict1: Первый словарь.
        dict2: Второй словарь.
        level: Уровень вложенности для отладки (по умолчанию 0).

    Возвращает:
        True, если словари равны; False в противном случае.
    """
    indent = "  " * level  # Уровень отступа для читаемости вывода
    print(f"{indent}Сравнение: {dict1} и {dict2}")

    keys1 = set(dict1.keys())
    keys2 = set(dict2.keys())

    if keys1 != keys2:
        missing_in_dict1 = keys2 - keys1
        missing_in_dict2 = keys1 - keys2
        print(f"{indent}Ключи не совпадают:")
        if missing_in_dict1:
            print(f"{indent}  Ключи отсутствуют в первом словаре: {missing_in_dict1}")
        if missing_in_dict2:
            print(f"{indent}  Ключи отсутствуют во втором словаре: {missing_in_dict2}")
        print(f"{indent}Выход из функции: словари не равны по ключам.")
        return False

    for key in dict1:
        val1 = dict1[key]
        val2 = dict2[key]

        # Проверка на вложенные словари
        if isinstance(val1, dict) and isinstance(val2, dict):
            if not compare_dicts(val1, val2, level + 1):
                print(f"{indent}Вложенные словари не равны для ключа '{key}'")
                print(f"{indent}Выход из функции: словари не равны по вложенным значениям.")
                return False
        elif val1 != val2:
            print(f"{indent}Значения не равны для ключа '{key}': {val1} != {val2}")
            print(f"{indent}Выход из функции: словари не равны по значению ключа '{key}'.")
            return False

    print(f"{indent}Словари равны на уровне {level}.")
    return True

In [78]:
dict_products = {}
arr_exists = []

In [12]:
def compare_products(product1: dict, product2: dict):
    if not product1["title"] == product2["title"]:
        arr_exists.append(product2)
        print(f'article number is exists: {product1["title"] == product2["title"]}')

        if not compare_dicts(product1["attributes"], product2["attributes"]):
            print("```")
            print(json.dumps(product1, ensure_ascii=False, indent=4))
            print(json.dumps(product2, ensure_ascii=False, indent=4))
            print("```")
        else:
            print("```")
            print(json.dumps({"link": product1["link"],
                                "title": product1["title"]}, ensure_ascii=False, indent=4))
            print(json.dumps({"link": product2["link"],
                                "title": product2["title"]}, ensure_ascii=False, indent=4))
            print("```")

In [79]:
for filename in json_filenames:
    with open(filename, "r", encoding="utf-8") as file:
        category_data = json.load(file)
    
    # print(category_data["category_name"])

    for product in category_data["products"]:
        product["category"] = [category_data["category_name"]]
        # print(product["link"])
        digits = extract_last_digits_from_url(product["link"])

        if digits not in dict_products:
            dict_products[digits] = product
        else:
            dict_products[digits]["category"] = list(set(dict_products[digits]["category"] + [category_data["category_name"]]))
            if len(dict_products[digits]["category"]) > 1:
                print(dict_products[digits]["title"], dict_products[digits]["category"])
            # compare_products(dict_products[digits], product)         
    


Мыльница М-Пластика пластиковая с крышкой ['Аксессуары и инвентарь для санузлов', 'Аксессуары для ванных комнат']
Ершик для унитаза Spin&clean Rock'n'Roll Original напольный без подставки из пластика цилиндрический белый ['Аксессуары и инвентарь для санузлов', 'Аксессуары для ванных комнат']
Мыльница пластиковая с крышкой №2 320-0503 ['Аксессуары и инвентарь для санузлов', 'Аксессуары для ванных комнат']
Ершик для унитаза Luscan напольный с подставкой из пластика цилиндрический белый ['Аксессуары и инвентарь для санузлов', 'Аксессуары для ванных комнат']
Ершик для унитаза Luscan напольный с подставкой из нержавеющей стали цилиндрический серебристый ['Аксессуары и инвентарь для санузлов', 'Аксессуары для ванных комнат']
Ершик для унитаза М-пластика напольный с подставкой из пластика цилиндрический серый ['Аксессуары и инвентарь для санузлов', 'Аксессуары для ванных комнат']
Ершик для унитаза Эвия напольный с подставкой из пластика круглый ['Аксессуары и инвентарь для санузлов', 'Аксессу

In [5]:
categories = []

In [6]:
for filename in json_filenames:
    with open(filename, "r", encoding="utf-8") as file:
        category_data = json.load(file)

    categories.append(category_data["category_name"])

In [15]:
products = list(dict_products.values())

In [7]:
for product in products:
    product["attributes"].pop("Малые закупки", None)

In [21]:
with open("dataset.json", "r", encoding="utf-8") as file:
    products = json.load(file)

In [24]:
with open("dataset.json", "w", encoding="utf-8") as file:
    json.dump(products, file, ensure_ascii=False)

In [23]:
for product in products:
    old_attributes = []
    new_attributes = {}

    for attribute, value in product["attributes"].items():
        if ", " in attribute:
            arr = attribute.split(', ')

            new_attribute = arr[0]
            dims = arr[1:]

            value = f'{value} {", ".join(dims)}'
            
            new_attributes[new_attribute] = value
            old_attributes.append(attribute)

    
    product["attributes"].update(new_attributes)

    for old_attribute in old_attributes:
        product['attributes'].pop(old_attribute, None)

In [25]:
attributes_set = set()

for product in products:
    for attribute, value in product["attributes"].items():
        if ", " in attribute:
            attributes_set.add(attribute)

print(*sorted(attributes_set), sep="\n")


In [14]:

for attribute in attributes_set:
    if len(attribute.split(', ')) > 2:
                print(attribute)
                print(attribute.split(', '))

Объем, мл/Вес, г
['Объем', 'мл/Вес', 'г']


In [9]:
data = {}

for filename in json_filenames:
    with open(filename, "r", encoding="utf-8") as file:
        category_data = json.load(file)

    if len(category_data["products"]) > 15:
        data[category_data["category_name"]] = category_data["products"]

In [208]:
import random

s = set()

while len(s )!= 100:
    s = set()
    random_choices = {}
    for category in random.choices(list(data.keys()), k = 20):
        if category not in random_choices:
            random_choices[category] = []

        for product in random.choices(data[category], k = 5 ):
            random_choices[category].append(extract_last_digits_from_url(product["link"]))

    for category in random_choices:
        s.update(random_choices[category])
    
len(s)

100

In [209]:
res = [dict_products[id] for id in s]
len(res)

for product in res:
    print(product["category"])

['Технические ткани']
['Диваны трехместные']
['Прочая техника для кухни']
['Форматная бумага']
['Наборы и корзины', 'Вкусности']
['Кабели и коннекторы', 'Кабели питания, шлейфы, переходники']
['Сварочные маски и аксессуары']
['Щетки и скребки автомобильные']
['Наборы и корзины', 'Бокалы, стаканы, стопки']
['Сварочные маски и аксессуары']
['Восковые карандаши,мелки']
['Фотобумага']
['Диваны трехместные']
['Фотобумага']
['Фотобумага']
['Входные коврики и напольные покрытия']
['Форматная бумага']
['Лотки и накопители для бумаг']
['Прочая техника для кухни']
['Входные коврики и напольные покрытия', 'Коврики входные']
['Форматная бумага']
['Продукты быстрого приготовления']
['Технические ткани']
['Сетевые кабели и коннекторы', 'Кабели и коннекторы']
['Холсты']
['Диваны трехместные']
['Ножи кухонные', 'Кухонный инвентарь']
['3D принтеры, сканеры и расходные материалы']
['3D принтеры, сканеры и расходные материалы']
['Лотки и накопители для бумаг']
['Продукты быстрого приготовления']
['Восков

In [211]:
products = res

for product in products:
    old_attributes = []
    new_attributes = {}

    for attribute, value in product["attributes"].items():
        if ", " in attribute:
            arr = attribute.split(', ')

            new_attribute = arr[0]
            dims = arr[1:]

            value = f'{value} {", ".join(dims)}'
            
            new_attributes[new_attribute] = value
            old_attributes.append(attribute)

    
    product["attributes"].update(new_attributes)

    for old_attribute in old_attributes:
        product['attributes'].pop(old_attribute, None)

with open("choice.json", "w", encoding="utf-8") as file:
    json.dump(products, file, ensure_ascii=False)